In [1]:
from dateutil.relativedelta import relativedelta
from sqlalchemy import create_engine
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import requests
import datetime
import argparse
import time
import re
import os

In [2]:
from dateutil.relativedelta import relativedelta
from sqlalchemy import create_engine
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import requests
import datetime
import argparse
import time
import re
import os

# league names
leagues = ['NHL','NLA','USHL','BCHL', 'SJHL', 'AHL','SuperElit', 'WHL',
           'CCHL','Jr. A SM-liiga','OHL','MHL','SHL','NCAA','Liiga', 
           'Allsvenskan','QMJHL','AJHL','OJHL','KHL','VHL','Czech','Czech2']

# start and end years to scrape data
start_year = 2005
end_year = 2019

# create season labels and get current season
seasons = [f'{s}-{s + 1}' for s in range(start_year, end_year + 1)]

# base url for ep website
base_url = 'https://www.eliteprospects.com'

# output meta data
tables = {
    'team_standing' : {'csv' : 'team_stats.csv',
                       'postgres' : 'team_stats'},
    'skaters' : {'csv' : 'skater_stats.csv',
                 'postgres' : 'skater_stats'},
    'goalies' : {'csv' : 'goalie_stats.csv',
                 'postgres' : 'goalie_stats'},
    'player_info' : {'csv' : 'player_info.csv',
                     'postgres' : 'player_info'},
         }

def get_unique_players(player_stats, goalie_stats):
    '''This function takes skater and goalie stats and returns list of unique 
    dataframe of playerids and player shortnames.
    '''
    player_cols = ['playerid', 'shortname']
    
    players = pd.concat([player_stats[player_cols].drop_duplicates(player_cols),
                         goalie_stats[player_cols].drop_duplicates(player_cols)])
    
    return players

def get_draft_eligibility(df):
    '''Return the first year a player is NHL draft eligible'''

    df.set_index('playerid', inplace=True)

    # create a series filled with valueus of Birth year + 18 on September 15th 
    draft_days = pd.to_datetime(dict(year=df.date_of_birth.dt.year.values + 18,
                        month=np.full((len(df), ), 9),
                        day=np.full((len(df), ), 15))) 

    draft_days.index = df.index

    # check if player will be 18 years old by September 15th of draft year
    df['draft_year_eligible'] = np.where((draft_days - df['date_of_birth']) / np.timedelta64(1, 'Y') >= 18,
                                             df.date_of_birth.dt.year.values + 18,
                                             df.date_of_birth.dt.year.values + 19) 

    return df.reset_index()

def get_current_year(date):
    '''Return hockey season label based on what the current date is'''
    if date.month >= 1 and date.month <= 9:
        return f'{date.year - 1}-{date.year}'

    else:
        return f'{date.year}-{date.year + 1}'

def load_db_credentials():
    '''Load database credentials from bash_profile'''

    user = os.environ['db_user']
    password = os.environ['db_pass']
    server = os.environ['db_host']
    database = os.environ['db_name']
    port = os.environ['db_port']

    return user, password, server, database, port

def output_to_db(df, name):
    '''Writes a dataframe to database using the table metadata outlined at script instantiation'''

    # get db credentials
    user, password, server, database, port = load_db_credentials()
    # create a connection to the database
    engine = create_engine(f'postgresql://{user}:{password}@{server}:{port}/{database}')
    # add a load date field
    df = df.assign(load_date = datetime.date.today())
    # write the values to the database
    df.to_sql(tables[name]['postgres'], engine, if_exists='append', index = False )

def output_to_csv(df, name):
    '''Writes a dataframe to csv file using the table metadata outlined at script instantiation'''
    table = tables[name]['csv']
    # write the values to the database
    df.to_sql(f'data/{table}', index=False)

def tidy_player_info(mydict, delete_keys):
    '''Remove keys from dictionary item that certain keys that do not want to be written to database'''

    keys_to_remove = set(delete_keys).intersection(set(mydict.keys()))
    for key in keys_to_remove:
        del mydict[key]

    return mydict

def get_draft_year(string):
    '''Using regular expression to return year a player was drafted from table row'''

    try:
        return dict(draft_year=re.split('[ ]', string)[0])
    except:
        return np.nan

def get_draft_round(string):
    '''Using regular expression to return round a player was drafted from table row'''

    try:
        return dict(draft_round=re.split('[ ]', string)[2])
    except:
        return np.nan

def get_draft_pick(string):
    '''Using regular expression to return the pick position a player was drafted from table row'''

    try:
        return dict(draft_pick=re.split('[ ]', string)[3].strip('#'))
    except:
        return np.nan

def get_draft_team(string):
    '''Using regular expression to return the team a player was drafted from table row'''

    try:
        return dict(draft_team=re.split('by', string)[1].strip())
    except:
        return np.nan

def get_team_rights(string):
    '''Using regular expression to return the current player rights from table row'''

    try:
        team, signed = string.split(' / ')
        return dict(rights=team, under_contract=True if signed == 'Signed' else False)
    except:
        return np.nan

def get_height(string):
    '''Using regular expression to return height in centimeter from table row'''

    try:
        return int(re.split('[/]', string)[1].strip('cm').strip())
    except:
        return np.nan

def get_weight(string):
    '''Using regular expression to return weight in kilograms from table row'''

    try:
        return int(re.split('[/]', string)[1].strip('kg').strip())
    except:
        return np.nan

def get_birthday(string):
    '''Using regular expression to extract player birthday from player url'''

    try:
        return re.split('[=&]', string)[1]
    except:
        return ''

def get_teamids(links):
    '''Using regular expression to return teamid from team url'''

    try:
        return [l.split('/')[4] for l in links]
    except:
        return ''

def get_shorthands(links):
    '''Using regular expression to return shorthands from url'''

    try:
        return [l.split('/')[5] for l in links]
    except:
        return ''

def get_playerids(links):
    '''Using regular expression to return playerid from player url'''

    try:
        return [l.split('/')[4] for l in links]
    except:
        return ''

def get_position(s):
    '''Using regular expression to return playerid from player url'''

    try:
        return re.search('\(([^)]+)', s).group(1).split('/')
    except:
        return ''

def clean_player_name(name):
    '''Using regular expression to return player name from table row'''

    return name[:np.negative(len(re.search('\(([^)]+)', name).group(1)) + 2)].strip()

def get_basic_player_info(soup):
    '''This function finds player details div and loops over the line items
    and creates a key/value dictionary containing player basic information'''

    player_details = soup.find('div', class_ = 'table-view')
    main_details = player_details.find('div', class_='row')

    player_info = {}

    for details in main_details.find_all('li'):
        key = details.find('div', class_='col-xs-4 fac-lbl-light').text.replace('\n','').strip()
        value = details.find('div', class_='col-xs-8 fac-lbl-dark')
        if (value.find('a')) and (key == 'Date of Birth'):
            # get birthday in better format
            value = get_birthday(value.find('a').get('href'))
        elif key == 'Height':
            value = get_height(value.text.replace('\n','').strip())
        elif key == 'Weight':
            value = get_weight(value.text.replace('\n','').strip())
        else:
            value = value.text.replace('\n','').strip()

        player_info['_'.join(key.lower().split(' '))] = value

    return player_info

def get_add_player_info(soup, player_info):
    '''This function finds player details unlisted div and loops over the line items
    and creates a key/value dictionary containing player additional information. Returns
    a merged dictionary of basic player info and additional player info.'''

    # additional info in unlisted list
    add_info = soup.find('section', class_='plyr_details').find_all('ul', class_ = 'list-unstyled')

    # interate over div to get draft information and signed status if exists
    draft_info = {}
    for list_ in add_info:
        for info in list_.find_all('li'):
            if info.find('div', class_='col-xs-3 fac-lbl-light'):
                key = info.find('div', class_='col-xs-3 fac-lbl-light').text.replace('\n','').strip()
                value = info.find('div', class_='col-xs-9 fac-lbl-dark').text.replace('\n','').strip()

                draft_info['_'.join(key.lower().split(' '))] = value

            if 'nhl_rights' in draft_info:
                draft_info = {**draft_info, **get_team_rights(draft_info['nhl_rights'])}
            if 'drafted' in draft_info:
                draft_info = {**draft_info, **get_draft_year(draft_info['drafted'])}
                draft_info = {**draft_info, **get_draft_round(draft_info['drafted'])}
                draft_info = {**draft_info, **get_draft_pick(draft_info['drafted'])}
                draft_info = {**draft_info, **get_draft_team(draft_info['drafted'])}

    return {**player_info, **draft_info}

def get_team_league_stats(league, year):
    '''This function takes a league name and year and retrieves standings and team stats. 
    Returns standings, teamidis and team shorthands to retrieve player roster information.'''
    # find current season
    current_season = get_current_year(datetime.date.today())

    # contruct url
    league_path = '-'.join(league.lower().split(' '))
    url = f'{base_url}/league/{league_path}/{year}'
    r = requests.get(url)
    soup = BeautifulSoup(r.text, features="lxml")

    # get standings
    standings = soup.find('table', {'class': 'table standings table-sortable'})

    team_links = [] # hyperlinks
    columns = ['team', 'gp', 'w', 't', 'l', 'otw',
               'otl', 'gf', 'ga', 'gd', 'tp'] # columns to return
    # get all rows for table
    table_rows = standings.find_all('tr')
    data = []
    for tr in table_rows:
        rows = []
        td = tr.find_all('td')
        # check if there are post season / playout / relegation stats
        if tr.attrs:
            if tr['class'][0] == 'title':
                header = tr.text.replace('\n','').strip()
                if header in ['Playout', 'Relegation']:
                    break
            
        for t in td:     
            try:
                if t['class'][0] in columns:
                    # if there is a link find the hyperlinks
                    if t.find('a'):
                        team_links.append(t.find('a').get('href'))
                    rows.append(t.text.replace('\n',''))
            except:
                # only add data that are contained in columns or have a class
                continue

        data.append(rows)

    team_standings = pd.DataFrame(data, columns=columns).dropna().replace(
        {'-': np.nan}).replace({'': np.nan}).replace({' - ': np.nan}).fillna(0)

    team_standings = team_standings.apply(pd.to_numeric, errors="ignore")
    # get team ids from url
    teamids = get_teamids(team_links)
    # get lowercase/hyphenated team name from url
    teamshorts = get_shorthands(team_links)
    # check team urls for current season
    if len(team_links[0].split('/')) != 7:
        team_links = [l + f'/{current_season}' for l in team_links]

    # add as metadata keys to df
    team_standings['season'] = year
    team_standings['teamid'] = teamids
    team_standings['shortname'] = teamshorts
    team_standings['url'] = team_links
    team_standings['league'] = league
    
    # aggregate regular season stats
    team_standings = team_standings.groupby(
        ['team', 'teamid', 'season', 'shortname', 'league', 'url']).sum().reset_index()

    return team_standings, team_standings.teamid, team_standings.shortname

def get_skater_stats(soup, year, teamid, teamshort, league):
    '''This function takes a teamid, team name and year and retrieves team skater stats. 
    Returns skater scoring data after calculating basic metrics.'''

    stats_table = soup.find('table',
                            {'class': 'table table-striped table-sortable skater-stats highlight-stats'})
    columns = ['season_stage', 'player', 'gp', 'g', 'a', 'tp', 'pim', 'pm']
    player_links = []

    # get all table rows from html table div minus title
    table_rows = stats_table.find_all('tr')[1:]
#     headers = set(stats_table.find_all('tr', class_ = ['title']))
#     table_rows -= headers

    data = []
    for tr in table_rows:
        # only retrieve regular season stats
        if tr.attrs:
            if 'class' in tr.attrs.keys():
                if tr['class'][0] == 'title':
                    header = tr.text.replace('\n','').strip()
                    if header != league and header[-1] != league:
                        season_stage = header
                        continue # don't want to add header to list of player stats
                    else:
                        season_stage = "Regular Season"
                        continue # don't want to add header to list of player stats
                    
        rows = [season_stage]
        td = tr.find_all('td')
        for t in td:
            try:
                if t['class'][0] in columns:
                    # if there is a link find the hyperlinks
                    if t.find('a'):
                        player_links.append(t.find('a').get('href'))
                    rows.append(t.text.replace('\n','').strip())
            except:
                # only add data that are contained in columns or have a class
                continue

        data.append(rows)

    # create dataframe for data
    player_stats = pd.DataFrame(data, columns=columns).dropna() # drop empty values
    player_stats = player_stats[player_stats.player != ''] # empty string players entries
    player_stats = player_stats.replace(
        {'-': np.nan}).replace({'': np.nan}).fillna(0).apply(pd.to_numeric, errors="ignore")

    # clean up dataframe -- add position, playerid, team info
    player_stats['position'] = player_stats.player.apply(get_position)
    player_stats['player'] = player_stats.player.apply(clean_player_name)
    player_stats['team'] = teamshort[:3].upper()
    player_stats['teamid'] = teamid
    player_stats['playerid'] = get_playerids(player_links)
    player_stats['year'] = year
    player_stats['url'] = player_links
    player_stats['shortname'] = get_shorthands(player_links)
    # calculate metrics for players
    player_stats = player_stats.groupby(['season_stage']).apply(calculate_player_metrics)

    return player_stats.droplevel(0)

def get_goalie_stats(soup, year, teamid, teamshort, league):
    '''This function takes a teamid, team name and year and retrieves team goalie stats. 
    Returns goalie scoring data.'''

    stats_table = soup.find('table',
                            {'class': 'table table-striped table-sortable goalie-stats highlight-stats'})
    columns = ['season_stage', 'player', 'gp', 'gaa', 'svp']

    goalie_links = []

    # get all table rows from html table div minus title
    table_rows = stats_table.find_all('tr')[1:]
#     headers = set(stats_table.find_all('tr', class_ = ['title']))
#     table_rows -= headers

    data = []
    for tr in table_rows:
        # only retrieve regular season stats
        if tr.attrs:
            if 'class' in tr.attrs.keys():
                if tr['class'][0] == 'title':
                    header = tr.text.replace('\n','').strip()
                    if header != league and header[-1] != league:
                        season_stage = header
                        continue # don't want to add header to list of player stats
                    else:
                        season_stage = "Regular Season"
                        continue # don't want to add header to list of player stats
                    
        rows = [season_stage]
        td = tr.find_all('td')
        for t in td:
            try:
                if t['class'][0] in columns:
                    # if there is a link find the hyperlinks
                    if t.find('a'):
                        goalie_links.append(t.find('a').get('href'))
                    rows.append(t.text.replace('\n','').strip())
            except:
                # only add data that are contained in columns or have a class
                continue

        data.append(rows)

    # create dataframe for data
    goalie_stats = pd.DataFrame(data, columns=columns).dropna() # drop empty values
    goalie_stats = goalie_stats[goalie_stats.player != ''] # empty string players entries
    goalie_stats = goalie_stats.replace(
    {'-': np.nan}).replace({'': np.nan}).fillna(0).apply(pd.to_numeric, errors="ignore")

    goalie_stats['team'] = teamshort[:3].upper()
    goalie_stats['teamid'] = teamid
    goalie_stats['playerid'] = get_playerids(goalie_links)
    goalie_stats['year'] = year
    goalie_stats['url'] = goalie_links
    goalie_stats['shortname'] = get_shorthands(goalie_links)

    return goalie_stats

def get_player_stats(year, teamid, teamshort, league):
    '''This function takes a teamid, team name and year and retrieves team goalie and skater stats. 
    Returns goalie / skater scoring data as a wrapper around individual position functions.'''

    # contruct url
    url = f'{base_url}/team/{teamid}/{teamshort}/{year}?tab=stats#players'
    r = requests.get(url)
    soup = BeautifulSoup(r.text, features="lxml")

#     try:
        # get stats from goalies and skaters
    return get_skater_stats(soup, year, teamid, teamshort, league), get_goalie_stats(soup, year, teamid, teamshort, league)

#     except:
#         print(f'\n{year} {teamshort} does not have have proper team stats \n')
#         return pd.DataFrame(columns=['player', 'gp', 'g',
#                                      'a', 'tp', 'pim', 'pm']), pd.DataFrame(columns=['player', 'gp',
#                                                                                      'gaa', 'svp'])

def calculate_player_metrics(df):
    '''Takes a dataframe containing player stats for a team and calcuates metrics intra-team.
    Returns points per game, assists per game, goals per game, percent of team points, etc.
    '''
    try:
        # adding metrics
        df = df.assign(
            gpg=(df.g.astype(int) / df.gp.astype(int)).round(3),
            apg=(df.a.astype(int) / df.gp.astype(int)).round(3),
            ppg=(df.tp.astype(int) / df.gp.astype(int)).round(3),
            perc_team_g=((df.g.astype(int) / df.gp) / (df.g.astype(int).sum() / df.gp.max())).round(3),
            perc_team_a=((df.a.astype(int) / df.gp) / (df.a.astype(int).sum() / df.gp.max())).round(3),
            perc_team_tp=((df.tp.astype(int) / df.gp) / (df.tp.astype(int).sum() / df.gp.max())).round(3))

        return df

    except:
        
        return df

def scrape_league_season_stats(league, year):
    '''This function is a wrapper takes a league name and year and retrieve team league
    standings data, skater scoring statistics, traditional goalie statistics. 
    '''

    print(f'\n--- Getting League Team Stats for {league} {year} --- \n')
    league_player_stats = []
    league_goalie_stats = []
    # get league standings for teams
    team_standings, teamids, teamshorts = get_team_league_stats(league, year)

    # loop over teams to construct player stat tables
    for teamid, teamshort in zip(teamids, teamshorts):
        print(f'--- Getting Team Player Stats for {teamshort} {teamid} ---')
        player_stats, goalie_stats = get_player_stats(year, teamid, teamshort, league)

        league_player_stats.append(player_stats)
        league_goalie_stats.append(goalie_stats)
        # space url calls by 1 second each time
        time.sleep(2)

    player_stats = pd.concat(league_player_stats, sort=False)
    goalie_stats = pd.concat(league_goalie_stats, sort=False)

    player_stats = player_stats.assign(league=league)
    goalie_stats = goalie_stats.assign(league=league)

    return team_standings, player_stats, goalie_stats

def get_player_info(playerid, shortname):
    ''' This function takes a playerid and player shortname and retrieve all scrapable 
    player information from their player page.
    '''

    print(f'--- Retrieving player info for: {shortname}')

    url = f'{base_url}/player/{playerid}/{shortname}'
    r = requests.get(url)
    soup = BeautifulSoup(r.text, features="lxml")

    delete_keys = ['age', 'youth_team', 'agency','highlights', 'position',
                   'drafted', 'cap_hit', 'nhl_rights', 'contract']

    player_info = get_basic_player_info(soup)
    player_info = get_add_player_info(soup, player_info)
    player_info = tidy_player_info(player_info, delete_keys)

    # space url calls by 1 second each time
    time.sleep(3)

    player_info = pd.DataFrame([player_info])
    player_info['date_of_birth'] = pd.to_datetime(player_info['date_of_birth'])
    player_info['playerid'] = playerid
    player_info['shortname'] = shortname

    return player_info

def full_data_load(output='csv'):
    '''This function is the main wrapper for a full load of elite prospects data. Leagues and Years
    are initialized, then looped over to retrieve team league standings, skater/goalie statistics and
    player information. Will always return a CSV output of the 4 main files and also has functionality 
    to update tables in a postgres database.
    '''

    # get date time of when script starts
    start = time.time()

    # initialize lists to hold data frames
    team_stats = []
    player_stats = []
    goalie_stats = []
    player_info = []

    for league in leagues:
        for year in seasons:
            try:
                # get team, skaters & goalies stats from league page
                teams, players, goalies = scrape_league_season_stats(league, year)
                team_stats.append(teams)
                player_stats.append(players)
                goalie_stats.append(goalies)

                # write data to database after each league season loaded
                if output == 'postgres':
                    output_to_db(teams, 'team_standing')
                    output_to_db(players, 'skaters')
                    output_to_db(goalies, 'goalies')

            except:
                print(f'\n---{league} {year} not found---\n')
                continue

    team_stats = pd.concat(team_stats, sort=False)
    player_stats = pd.concat(player_stats, sort=False)
    goalie_stats = pd.concat(goalie_stats, sort=False)
    # get player info for skaters and goalies
    players = get_unique_players(player_stats, goalie_stats)

    for playerid, shortname in zip(players.playerid, players.shortname):
        try:
            player = get_player_info(playerid, shortname)
            player_info.append(player)
        except:
            print(f'--- {shortname} bad player data ---')
            continue
    
    player_info = pd.concat(player_info, sort=False)
    # gets draft eligibility for all players
    player_info = get_draft_eligibility(player_info)

    if output == 'postgres':
        output_to_db(player_info, 'player_info')

    # output to csv always
    output_to_csv(team_stats, 'team_standing')
    output_to_csv(player_stats, 'skaters')
    output_to_csv(goalie_stats, 'goalies')
    output_to_csv(player_info, 'player_info')

    print('Runtime : {} mins'.format(round((time.time() - start) / 60 ,2)))

def main(output):
    full_data_load(output)

In [3]:
full_data_load('postgres')


--- Getting League Team Stats for NHL 2005-2006 --- 

--- Getting Team Player Stats for atlanta-thrashers 51 ---
--- Getting Team Player Stats for boston-bruins 52 ---
--- Getting Team Player Stats for buffalo-sabres 53 ---
--- Getting Team Player Stats for calgary-flames 54 ---
--- Getting Team Player Stats for carolina-hurricanes 55 ---
--- Getting Team Player Stats for chicago-blackhawks 56 ---
--- Getting Team Player Stats for colorado-avalanche 57 ---
--- Getting Team Player Stats for columbus-blue-jackets 58 ---
--- Getting Team Player Stats for dallas-stars 59 ---
--- Getting Team Player Stats for detroit-red-wings 60 ---
--- Getting Team Player Stats for edmonton-oilers 61 ---
--- Getting Team Player Stats for florida-panthers 62 ---
--- Getting Team Player Stats for los-angeles-kings 79 ---
--- Getting Team Player Stats for mighty-ducks-of-anaheim 1580 ---
--- Getting Team Player Stats for minnesota-wild 63 ---
--- Getting Team Player Stats for montreal-canadiens 64 ---
--- G

--- Getting Team Player Stats for montreal-canadiens 64 ---
--- Getting Team Player Stats for nashville-predators 65 ---
--- Getting Team Player Stats for new-jersey-devils 66 ---
--- Getting Team Player Stats for new-york-islanders 67 ---
--- Getting Team Player Stats for new-york-rangers 68 ---
--- Getting Team Player Stats for ottawa-senators 69 ---
--- Getting Team Player Stats for philadelphia-flyers 70 ---
--- Getting Team Player Stats for phoenix-coyotes 72 ---
--- Getting Team Player Stats for pittsburgh-penguins 71 ---
--- Getting Team Player Stats for san-jose-sharks 73 ---
--- Getting Team Player Stats for st.-louis-blues 74 ---
--- Getting Team Player Stats for tampa-bay-lightning 75 ---
--- Getting Team Player Stats for toronto-maple-leafs 76 ---
--- Getting Team Player Stats for vancouver-canucks 77 ---
--- Getting Team Player Stats for washington-capitals 78 ---

--- Getting League Team Stats for NHL 2010-2011 --- 

--- Getting Team Player Stats for anaheim-ducks 1580 --

--- Getting Team Player Stats for anaheim-ducks 1580 ---
--- Getting Team Player Stats for arizona-coyotes 72 ---
--- Getting Team Player Stats for boston-bruins 52 ---
--- Getting Team Player Stats for buffalo-sabres 53 ---
--- Getting Team Player Stats for calgary-flames 54 ---
--- Getting Team Player Stats for carolina-hurricanes 55 ---
--- Getting Team Player Stats for chicago-blackhawks 56 ---
--- Getting Team Player Stats for colorado-avalanche 57 ---
--- Getting Team Player Stats for columbus-blue-jackets 58 ---
--- Getting Team Player Stats for dallas-stars 59 ---
--- Getting Team Player Stats for detroit-red-wings 60 ---
--- Getting Team Player Stats for edmonton-oilers 61 ---
--- Getting Team Player Stats for florida-panthers 62 ---
--- Getting Team Player Stats for los-angeles-kings 79 ---
--- Getting Team Player Stats for minnesota-wild 63 ---
--- Getting Team Player Stats for montreal-canadiens 64 ---
--- Getting Team Player Stats for nashville-predators 65 ---
--- Getting

--- Getting Team Player Stats for nashville-predators 65 ---
--- Getting Team Player Stats for new-jersey-devils 66 ---
--- Getting Team Player Stats for new-york-islanders 67 ---
--- Getting Team Player Stats for new-york-rangers 68 ---
--- Getting Team Player Stats for ottawa-senators 69 ---
--- Getting Team Player Stats for philadelphia-flyers 70 ---
--- Getting Team Player Stats for pittsburgh-penguins 71 ---
--- Getting Team Player Stats for san-jose-sharks 73 ---
--- Getting Team Player Stats for st.-louis-blues 74 ---
--- Getting Team Player Stats for tampa-bay-lightning 75 ---
--- Getting Team Player Stats for toronto-maple-leafs 76 ---
--- Getting Team Player Stats for vancouver-canucks 77 ---
--- Getting Team Player Stats for vegas-golden-knights 22211 ---
--- Getting Team Player Stats for washington-capitals 78 ---
--- Getting Team Player Stats for winnipeg-jets 9966 ---

--- Getting League Team Stats for NHL 2019-2020 --- 

--- Getting Team Player Stats for anaheim-ducks 15

/Users/connorjung/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:492: RuntimeWarning: invalid value encountered in long_scalars
/Users/connorjung/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:493: RuntimeWarning: invalid value encountered in long_scalars
/Users/connorjung/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:494: RuntimeWarning: invalid value encountered in long_scalars


...

--- Retrieving player info for: rock-boynton
--- Retrieving player info for: william-rawski
--- Retrieving player info for: will-barber
--- Retrieving player info for: connor-winters
--- connor-winters bad player data ---
--- Retrieving player info for: nicholas-kidd
--- Retrieving player info for: luca-durante
--- Retrieving player info for: patrick-o-leary
--- Retrieving player info for: tyler-caruana
--- Retrieving player info for: jack-brand
--- Retrieving player info for: chris-elliott
--- Retrieving player info for: brendon-landry
--- Retrieving player info for: jake-fleming
--- Retrieving player info for: jacob-gordon
--- Retrieving player info for: nicholas-mueller
--- Retrieving player info for: tyler-fassl
--- Retrieving player info for: elliot-gerth
--- Retrieving player info for: charles-grimard
--- Retrieving player info for: pierce-nelson
--- Retrieving player info for: victor-olivier-courchesne
--- Retrieving player info for: cale-mcwilliams
--- Retrieving player info fo

--- Retrieving player info for: sergei-ageyev
--- Retrieving player info for: alexei-yakhin
--- Retrieving player info for: martin-falter
--- Retrieving player info for: edgars-lusins
--- Retrieving player info for: travis-scott
--- Retrieving player info for: konstantin-chashchukhin
--- Retrieving player info for: maris-jucers
--- Retrieving player info for: jan-laco
--- Retrieving player info for: nikita-davydov
--- Retrieving player info for: vladimir-zhuldikov
--- Retrieving player info for: stepan-goryachevskikh
--- Retrieving player info for: ondrej-kocian
--- Retrieving player info for: marcel-melichercik
--- Retrieving player info for: branislav-konrad
--- Retrieving player info for: alexander-tryanichev
--- Retrieving player info for: timur-bilyalov
--- Retrieving player info for: mikhail-meyer
--- Retrieving player info for: dmitri-malgin
--- Retrieving player info for: jakub-sedlacek
--- Retrieving player info for: pavel-yachnik
--- Retrieving player info for: dmitri-milchak

--- Retrieving player info for: lukas-sablik
--- Retrieving player info for: jakub-cech
--- Retrieving player info for: marek-novotny
--- Retrieving player info for: dalibor-sedlar
--- Retrieving player info for: lukas-cikanek
--- Retrieving player info for: antonin-stelmach
--- Retrieving player info for: vladimir-hudacek
--- Retrieving player info for: lukas-danecek
--- Retrieving player info for: michal-holes
--- Retrieving player info for: stefan-zigardy
--- Retrieving player info for: dusan-salficky
--- Retrieving player info for: david-adamec
--- Retrieving player info for: petr-tucek
--- Retrieving player info for: jiri-muller
--- Retrieving player info for: tomas-sturala
--- Retrieving player info for: jure-verlic
--- Retrieving player info for: michal-fikrt
--- Retrieving player info for: tomas-zavorka
--- Retrieving player info for: martin-volke
--- Retrieving player info for: jiri-zikmund
--- Retrieving player info for: tomas-hiadlovsky
--- Retrieving player info for: jarosl

--- Retrieving player info for: martin-frolik
--- Retrieving player info for: jan-jira
--- Retrieving player info for: tomas-sork
--- Retrieving player info for: jiri-skubal
--- Retrieving player info for: vojtech-skliba
--- Retrieving player info for: michal-meravy
--- Retrieving player info for: roman-boska
--- Retrieving player info for: jiri-blazek
--- Retrieving player info for: michal-mahdal
--- Retrieving player info for: adam-wolf
--- Retrieving player info for: martin-sejpal
--- Retrieving player info for: jakub-jelinek
--- Retrieving player info for: daniel-vokal
--- Retrieving player info for: hynek-kudela
--- Retrieving player info for: tomas-mastik
--- Retrieving player info for: dominik-chabr
--- Retrieving player info for: jan-bryl
--- Retrieving player info for: vaclav-hoffmann
--- Retrieving player info for: marek-mazuch
--- Retrieving player info for: vit-lehecka
--- Retrieving player info for: tomas-kafka
--- Retrieving player info for: matej-skuta
--- Retrieving pla

TypeError: to_sql() missing 1 required positional argument: 'con'

### Adding Player Info that's missing due to IP lock

In [45]:
# load database credentials and create connection
user, password, server, database, port = load_db_credentials()
engine = create_engine(f'postgresql://{user}:{password}@{server}:{port}/{database}')

all_skaters = pd.read_sql(''' select distinct playerid, shortname from skater_stats ''', engine)
all_goalies = pd.read_sql(''' select distinct playerid, shortname from goalie_stats ''', engine)
info = pd.read_sql(''' select distinct playerid, shortname from player_info ''', engine)

all_players = pd.concat([all_skaters,
                         all_goalies], sort=False)

players = all_players[all_players.playerid.isin(list(set(all_players.playerid) - set(info.playerid)))]

In [71]:
player_info = []

for playerid, shortname in zip(players.playerid, players.shortname):
    try:
        player = get_player_info(playerid, shortname)
        player_info.append(player)
    except:
        print(f'--- {shortname} bad player data ---')
        continue

player_info = pd.concat(player_info, sort=False)
# gets draft eligibility for all players
player_info = get_draft_eligibility(player_info)



--- Retrieving player info for: josh-chase
--- Retrieving player info for: jesse-hudkins
--- Retrieving player info for: otto-mild
--- Retrieving player info for: graham-watson
--- Retrieving player info for: logan-gorsalitz
--- Retrieving player info for: barnabas-birkeland
--- Retrieving player info for: ryan-chynoweth
--- Retrieving player info for: peter-stratis
--- Retrieving player info for: martin-curda
--- Retrieving player info for: miroslav-juda
--- Retrieving player info for: jaroslav-flieger
--- Retrieving player info for: darren-nesbitt
--- Retrieving player info for: gleb-bobin
--- Retrieving player info for: matthew-whittaker
--- Retrieving player info for: christopher-blair
--- Retrieving player info for: igor-safaraleyev
--- Retrieving player info for: ashton-casault
--- Retrieving player info for: alexander-kadeykin
--- Retrieving player info for: eddie-ahlmark
--- Retrieving player info for: oleg-nazarov
--- Retrieving player info for: toni-lehikoinen
--- Retrieving 

--- Retrieving player info for: grigori-ponkratov
--- Retrieving player info for: corey-ronan
--- Retrieving player info for: yevgeni-vilensky
--- Retrieving player info for: rasmus-hemstrom
--- Retrieving player info for: matti-pinomaki
--- Retrieving player info for: mike-wills
--- Retrieving player info for: pavel-kim
--- Retrieving player info for: jegors-mateiko
--- Retrieving player info for: danil-makarov
--- Retrieving player info for: alvari-rautiainen
--- Retrieving player info for: tommy-tanner
--- Retrieving player info for: warren-steele
--- Retrieving player info for: michal-skoumal
--- Retrieving player info for: nolan-descoteaux
--- Retrieving player info for: david-blazek
--- Retrieving player info for: radek-slama
--- Retrieving player info for: andrei-galushkin
--- Retrieving player info for: niko-snellman
--- Retrieving player info for: lauri-viitanen
--- Retrieving player info for: matt-hedrick
--- Retrieving player info for: arslan-akhmetyanov
--- Retrieving playe

--- Retrieving player info for: oleg-korchagin
--- Retrieving player info for: francis-thibeault
--- Retrieving player info for: igor-bondyrev
--- Retrieving player info for: joonas-jalvanti
--- Retrieving player info for: james-doering
--- Retrieving player info for: ruslan-sadretdinov
--- Retrieving player info for: vladislav-tsurikov
--- Retrieving player info for: eero-hyvarinen
--- Retrieving player info for: jeremy-gottzmann
--- Retrieving player info for: jonathan-hill
--- Retrieving player info for: stefan-lassen
--- Retrieving player info for: vincent-bernier
--- Retrieving player info for: lorne-tessier
--- Retrieving player info for: juuso-nieminen
--- Retrieving player info for: peter-tiivola
--- Retrieving player info for: tim-fallowfield
--- Retrieving player info for: filip-dvorak
--- Retrieving player info for: artyom-gladkov
--- Retrieving player info for: zack-di-cesare
--- Retrieving player info for: brennan-menard
--- Retrieving player info for: jason-goodship
--- R

--- Retrieving player info for: grayson-arnott
--- Retrieving player info for: ty-lasker
--- Retrieving player info for: niko-helavirta
--- Retrieving player info for: tyler-cooke
--- Retrieving player info for: ivan-shirokalov
--- Retrieving player info for: branislav-fabry
--- Retrieving player info for: hyun-ho-jang
--- hyun-ho-jang bad player data ---
--- Retrieving player info for: patrick-walsh
--- Retrieving player info for: jacob-gaucher
--- Retrieving player info for: mikhail-romanychev
--- Retrieving player info for: matt-hounslow
--- Retrieving player info for: david-homer
--- Retrieving player info for: kyle-wilhelm
--- Retrieving player info for: philippe-bergeron
--- Retrieving player info for: anton-abrarov
--- Retrieving player info for: matthew-danner
--- Retrieving player info for: carter-wolski
--- Retrieving player info for: damir-galin
--- Retrieving player info for: zdenek-hrouda
--- Retrieving player info for: dominik-crnogorac
--- Retrieving player info for: tom

--- Retrieving player info for: anton-pritykin
--- Retrieving player info for: maxim-zyuzyakin
--- Retrieving player info for: marko-sakic
--- Retrieving player info for: anton-yefremov
--- Retrieving player info for: cory-lauer
--- Retrieving player info for: dan-caccavella
--- Retrieving player info for: franco-colapaolo
--- Retrieving player info for: ryan-maguire
--- Retrieving player info for: jared-seminoff
--- Retrieving player info for: jeremy-quenneville
--- Retrieving player info for: casey-purpur
--- Retrieving player info for: yegor-sofyin
--- Retrieving player info for: patrick-marsh
--- Retrieving player info for: robert-kantor
--- Retrieving player info for: ivan-savin
--- Retrieving player info for: kevin-o-connor
--- Retrieving player info for: anton-sjoberg
--- Retrieving player info for: mark-walchuk
--- Retrieving player info for: vladislav-skorokhodov
--- Retrieving player info for: vadim-kucherov
--- Retrieving player info for: chris-meininger
--- Retrieving playe

...

--- Retrieving player info for: gary-johal
--- Retrieving player info for: malcolm-walilko
--- Retrieving player info for: isak-johansson
--- Retrieving player info for: emil-jidskog
--- Retrieving player info for: cam-ward
--- Retrieving player info for: mikhail-kuzmin
--- Retrieving player info for: luke-bierworth
--- Retrieving player info for: lars-johansson
--- Retrieving player info for: ryan-zapolski
--- Retrieving player info for: noah-featherstonhaugh-gowe
--- Retrieving player info for: matt-walsh
--- Retrieving player info for: yevgeni-kandyba
--- Retrieving player info for: rasmus-reijola
--- Retrieving player info for: pavel-davydyuk
--- Retrieving player info for: dryden-mckay
--- Retrieving player info for: alexander-emanuelsson
--- Retrieving player info for: nicholas-pineo
--- Retrieving player info for: nick-king
--- Retrieving player info for: francis-leonard-mayer
--- Retrieving player info for: ty-marcinkowski
--- Retrieving player info for: teemu-lassila
--- Retri

--- Retrieving player info for: scott-diebold
--- Retrieving player info for: russ-brownell
--- Retrieving player info for: kevin-ackley
--- Retrieving player info for: alexandre-labreche
--- alexandre-labreche bad player data ---
--- Retrieving player info for: jesse-shoeman
--- Retrieving player info for: marty-turco
--- Retrieving player info for: dershahn-stewart
--- Retrieving player info for: pascal-muller-larsson
--- Retrieving player info for: ryan-anderson
--- Retrieving player info for: michael-stiliadis
--- Retrieving player info for: alex-rolfe
--- Retrieving player info for: petteri-simila
--- Retrieving player info for: jason-kasdorf
--- Retrieving player info for: drew-macintyre
--- Retrieving player info for: eikka-kokkonen
--- Retrieving player info for: nicholas-malvin
--- Retrieving player info for: mike-spillane
--- Retrieving player info for: jesper-myrenberg
--- Retrieving player info for: tom-draper
--- Retrieving player info for: aku-ripatti
--- Retrieving playe

--- Retrieving player info for: johannes-kukkonen
--- Retrieving player info for: vladislav-dmitriyev
--- Retrieving player info for: john-cullen
--- Retrieving player info for: tero-tuomarila
--- Retrieving player info for: danil-shaloiko
--- Retrieving player info for: adam-kraus
--- Retrieving player info for: nate-hardy
--- Retrieving player info for: jared-beaulieu
--- Retrieving player info for: brad-roberts
--- Retrieving player info for: john-roberts
--- Retrieving player info for: yaniv-perets
--- Retrieving player info for: hampus-lofgren
--- Retrieving player info for: tanner-mcgaw
--- Retrieving player info for: tomas-klestil
--- Retrieving player info for: michael-garnett
--- Retrieving player info for: andrei-sukhanov
--- Retrieving player info for: mikhail-finagin
--- Retrieving player info for: dustin-nickel
--- Retrieving player info for: brian-boucher
--- Retrieving player info for: ryan-wadden
--- Retrieving player info for: fredrik-holmgren
--- Retrieving player inf

--- Retrieving player info for: anthony-felice
--- Retrieving player info for: kris-moore
--- Retrieving player info for: brett-epp
--- Retrieving player info for: chris-collins
--- Retrieving player info for: benjamin-conz
--- Retrieving player info for: dusan-salficky
--- Retrieving player info for: artyom-gvozdik
--- Retrieving player info for: zackarias-skog
--- Retrieving player info for: adam-svach
--- Retrieving player info for: romi-huunonen
--- Retrieving player info for: stefan-ridderwall
--- Retrieving player info for: dean-shatzer
--- Retrieving player info for: daniel-wenham
--- Retrieving player info for: artyom-martynov
--- Retrieving player info for: brendan-burke
--- Retrieving player info for: james-povall
--- Retrieving player info for: alex-wisco
--- Retrieving player info for: andrew-shortridge
--- Retrieving player info for: alex-kolkkinen
--- Retrieving player info for: forbes-anderson
--- Retrieving player info for: michael-caluori
--- Retrieving player info for

ProgrammingError: (psycopg2.errors.UndefinedColumn) column "catches" of relation "player_info" does not exist
LINE 1: ...und, draft_pick, draft_team, nhl_draft, rankings, catches, d...
                                                             ^

[SQL: INSERT INTO player_info (playerid, date_of_birth, place_of_birth, nation, height, weight, shoots, status, shortname, rights, under_contract, draft_year, draft_round, draft_pick, draft_team, nhl_draft, rankings, catches, draft_year_eligible, load_date) VALUES (%(playerid)s, %(date_of_birth)s, %(place_of_birth)s, %(nation)s, %(height)s, %(weight)s, %(shoots)s, %(status)s, %(shortname)s, %(rights)s, %(under_contract)s, %(draft_year)s, %(draft_round)s, %(draft_pick)s, %(draft_team)s, %(nhl_draft)s, %(rankings)s, %(catches)s, %(draft_year_eligible)s, %(load_date)s)]
[parameters: ({'playerid': '32958', 'date_of_birth': datetime.datetime(1982, 1, 9, 0, 0), 'place_of_birth': 'Big Rapids, MI, USA', 'nation': 'USA', 'height': 173.0, 'weight': 77

In [77]:
player_info.drop(columns=['catches'], inplace=True)

In [78]:
output_to_db(player_info, 'player_info')

### debugging

In [3]:
teams, players, goalies = scrape_league_season_stats('NHL', '2005-2006')


--- Getting League Team Stats for NHL 2005-2006 --- 

--- Getting Team Player Stats for atlanta-thrashers 51 ---
--- Getting Team Player Stats for boston-bruins 52 ---
--- Getting Team Player Stats for buffalo-sabres 53 ---
--- Getting Team Player Stats for calgary-flames 54 ---
--- Getting Team Player Stats for carolina-hurricanes 55 ---
--- Getting Team Player Stats for chicago-blackhawks 56 ---
--- Getting Team Player Stats for colorado-avalanche 57 ---
--- Getting Team Player Stats for columbus-blue-jackets 58 ---
--- Getting Team Player Stats for dallas-stars 59 ---
--- Getting Team Player Stats for detroit-red-wings 60 ---
--- Getting Team Player Stats for edmonton-oilers 61 ---
--- Getting Team Player Stats for florida-panthers 62 ---
--- Getting Team Player Stats for los-angeles-kings 79 ---
--- Getting Team Player Stats for mighty-ducks-of-anaheim 1580 ---
--- Getting Team Player Stats for minnesota-wild 63 ---
--- Getting Team Player Stats for montreal-canadiens 64 ---
--- G

In [6]:
df = pd.read_csv('../../prospect_database/player_season_stats.csv')


/Users/connorjung/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3049: DtypeWarning: Columns (32,33) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [168]:
df[(df.shortname == 'jesse-ylonen')]

Unnamed: 0  playerid        player position  ... end_year season_age real_season_age next_season
11312       79491    299117  Jesse Ylönen     {RW}  ...     2017         18           18.25   2017-2018
57468       79492    299117  Jesse Ylönen     {RW}  ...     2019         20           20.24   2019-2020
71030       79493    299117  Jesse Ylönen     {RW}  ...     2020         21           21.25   2020-2021

[3 rows x 41 columns]

In [182]:
teams

team teamid                                    shortname league  ...   gf   ga  gd   tp
0               BK Mlada Boleslav    699                            bk-mlada-boleslav  Czech  ...  156  164  -8   72
1              Bili Tygri Liberec    700                           bili-tygri-liberec  Czech  ...  128  131  -3   69
2         HC Energie Karlovy Vary    153                      hc-energie-karlovy-vary  Czech  ...  110  146 -36   62
3                  HC Kometa Brno   1190                               hc-kometa-brno  Czech  ...  153  135  18   95
4                     HC Litvinov    155                                  hc-litvinov  Czech  ...  167  120  47  105
5               HC Ocelari Trinec    161                            hc-ocelari-trinec  Czech  ...  183  117  66  107
6                      HC Olomouc   1240                                   hc-olomouc  Czech  ...  126  167 -41   54
7                        HC Plzen    637                                     hc-plzen  Czech  ...  144  133  11   75
8                 HC Slavia Praha    162                              hc-slavia-praha  Czech  ...  106  181 -75   44
9                 HC Sparta Praha    164                              hc-sparta-praha  Czech  ...  194  140  54   94
10             HC Vitkovice Steel    772                           hc-vitkovice-steel  Czech  ...  136  153 -17   75
11   HC ČSOB Pojišťovna Pardubice    159  hc-%C4%8Csob-poji%C5%A1%C5%A5ovna-pardubice  Czech  ...  143  156 -13   74
12              HK Hradec Kralove  15659                            hk-hradec-kralove  Czech  ...  136  131   5   85
13                       PSG Zlín    156                                     psg-zlin  Czech  ...  145  153  -8   81

[14 rows x 15 columns]